<a href="https://colab.research.google.com/github/Vaibhavs10/notebooks/blob/main/zephyr_assisted_musicgen_generations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# [MusicGen](https://huggingface.co/facebook/musicgen-stereo-medium) Prompt Upsampling w/ [Zephyr](https://huggingface.co/HuggingFaceH4/zephyr-7b-beta) 🎶

put together by [VB](https://twitter.com/reach_vb)

## Set up the developement environment

In [2]:
!pip install -q --upgrade huggingface_hub git+https://github.com/huggingface/transformers.git

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 311.7/311.7 kB 6.7 MB/s eta 0:00:00


## Initialise the text to audio pipeline in Transformers

In [3]:
import torch
from transformers import pipeline

vibes = pipeline("text-to-audio",
                 "facebook/musicgen-stereo-medium",
                 torch_dtype=torch.float16,
                 device="cuda")

config.json:   0%|          | 0.00/7.75k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/4.07G [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


generation_config.json:   0%|          | 0.00/224 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.8k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.20k [00:00<?, ?B/s]

## Setup an InferenceClient

This allows us to avoid downloading Zephyr weights and we directly use the [InferenceClient](https://huggingface.co/docs/huggingface_hub/package_reference/inference_client) to run Zephyr!

Note: You'd need your HF_TOKEN (get it from [http://hf.co/settings/token](http://hf.co/settings/token) 🤗

In [11]:
from huggingface_hub import InferenceClient

HF_TOKEN = "PUT YOUR TOKEN HERE"

client = InferenceClient(model="HuggingFaceH4/zephyr-7b-beta",
                         token=HF_TOKEN)

## Define your Prompt (keywords are fine too)

In [ ]:
prompt = "Tunes invokes the feeling of happiness and calmess. Highly captivating. Lo-fi. Beatles style."

In [19]:
input = f"Take the next sentence and enrich it with details, keep it compact. {prompt}"

output = client.text_generation(input, max_new_tokens=100)

print(output)



The sound of the piano keys being pressed, the soft melody that follows, and the gentle hum of the bass create a soothing atmosphere that envelops the listener. It's as if the music is a warm embrace, inviting you to relax and unwind. The rhythm is slow and steady, like a heartbeat, and the notes dance together in perfect harmony. It's a symphony of peace and tranquility, a lullaby for the soul.


## Pass the LLM output to musicgen

In [16]:
out = vibes(output)

Using the model-agnostic default `max_length` (=1500) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.


## Voila! Listen to your LLM assisted creation!

In [17]:
from IPython.display import Audio

Audio(out["audio"][0], rate=32000)

## Better yet, save it in a file!

In [18]:
import soundfile as sf

sampling_rate = 32000
audio_values = out["audio"]
sf.write("musicgen_lofi.wav", audio_values[0].T, sampling_rate)